In [1]:
import pandas as pd
import numpy as np
import os
from datetime import date
import datetime
import time
from tqdm import tqdm
import yfinance as yf
from sklearn.decomposition import PCA
from sklearn.preprocessing import MinMaxScaler
pd.set_option('display.max_rows', 10000)

# Class for aggregating longitudinally

In [2]:
class CreateLongData:
    """
    """
    def __init__(self, directory, df):
        self.directory = directory
        self.df = df

    def usa_stocks(self, date):
        files = os.listdir(f"{self.directory}/{date}")
        usa_stocks_file = [x for x in files if (x.startswith('usa_stocks')) & (x.endswith('.csv'))][0]
        df = pd.read_csv(f"{self.directory}/{date}/{usa_stocks_file}").iloc[:, 1:]
        # remove % from values
        df = df.replace({'%':''}, regex=True) 
        # no change during after hours
        df['After-Hours Change'] = df['After-Hours Change'].replace(np.nan, 0) 
        # drop fundamentals for now
        df = df.drop(['Company', 'Country', 'P/E', 'Forward P/E', 'P/B', 'Dividend Yield', 'Total Debt/Equity',
                      'EPS growth this year', 'EPS growth next year'], axis=1) 
        # remove stock with missing market cap data
        df = df[~df['Market Cap'].isna()] 
        # remove remaining stock with missing either instituional ownership, float short, short ratio, volatility, rsi
        df = df.dropna() 
        # ensure all columns are numerics
        df = pd.concat([df[['Ticker', 'Sector', 'Industry']], df.drop(['Ticker', 'Sector', 'Industry'], axis=1).apply(pd.to_numeric)], axis=1)
        # convert % to decimals
        perc_cols = ['Dividend Yield','EPS growth this year','EPS growth next year','Institutional Ownership',
                     'Institutional Transactions','Float Short','Performance (Week)','Performance (Month)',
                     'Volatility (Week)','Volatility (Month)','20-Day Simple Moving Average','50-Day Simple Moving Average',
                     '200-Day Simple Moving Average','50-Day High','50-Day Low','52-Week High','52-Week Low',
                     'Relative Strength Index (14)','Change from Open','Gap','Change','After-Hours Change']
        df[list(set(df.columns).intersection(set(perc_cols)))] = df[list(set(df.columns).intersection(set(perc_cols)))]/100
        # clean up column names
        df.columns = df.columns.str.replace("(", "")
        df.columns = df.columns.str.replace(")", "")
        df.columns = df.columns.str.replace("-", "_")
        df.columns = df.columns.str.replace(" ", "_")
        # add date
        df['date'] = datetime.datetime.strptime(date, '%m-%d-%Y')
        return df

    def technical_signals(self, date, df_all):
        files = os.listdir(f"{self.directory}/{date}")
        signal_files = [x for x in files if ((x.startswith('signal')) | (x.startswith('dv'))) & (x.endswith('.csv'))]
        # iterate through all technical indicators
        for i in signal_files:
            # for each stock flagged by the specified technical indicator in the filename, join to main df
            df_signal = pd.read_csv(f"{self.directory}/{date}/{i}").iloc[:, 1:]
            signal_col = i.replace('.csv','')
            # 1 for technical indicator satisfied
            df_signal[signal_col] = 1
            df_all = df_all.merge(df_signal, on='Ticker', how='left')
            # 0 if technical indicator not satisfied
            df_all[signal_col] = df_all[signal_col].replace(np.nan, 0)         
        return df_all
    
    def get_vix(self):
        end = date.today() + datetime.timedelta(days=1)
        start = self.df['date'].min()
        vix = yf.download('^VIX', start=start, end=end)
        vix = vix.reset_index()
        vix_close = vix[['Date', 'Close']].rename(columns={'Close':'vix', 'Date':'date'})
        return vix_close
    
    def create_lag_feats(self, df, num_lags=1):
        # lag all current_ columns
        df_lag = df.copy()
        current_cols = [x for x in df_lag.columns if x.startswith('current')]
        for i in tqdm(range(1, num_lags + 1)):
            for j in current_cols:
                col_name = j.replace('current', f"previous{i}")
                df_lag[col_name] = df_lag.groupby('ticker')[j].shift(i)
        return df_lag
    
    def create_dv(self, df):
        df_dv = df.copy()
        # create dependent variables based off current features
        df_dv['dv_5perc_inc_from_open'] = np.select([df_dv['current_change_from_open'] >= 0.05,
                                                     df_dv['current_change_from_open'] <= 0], [1, 0], np.nan)
        df_dv['dv_2perc_inc_from_open'] = np.select([df_dv['current_change_from_open'] >= 0.02,
                                                     df_dv['current_change_from_open'] <= 0], [1, 0], np.nan)
        df_dv['dv_1perc_inc_from_open'] = np.select([df_dv['current_change_from_open'] >= 0.01,
                                                     df_dv['current_change_from_open'] <= 0], [1, 0], np.nan)
        df_dv['dv_close_up_from_open'] = np.select([df_dv['current_change_from_open'] > 0,
                                                    df_dv['current_change_from_open'] <= 0], [1, 0], np.nan)
        df_dv['dv_top_gainer'] = np.select([(df_dv['current_candlestick_marubozu_white'] == 1) |
                                            (df_dv['current_indicator_top_gainers'] == 1),
                                            df_dv['current_change_from_open'] <= 0], [1, 0], np.nan) 
        df_dv['dv_doji'] = np.where((df_dv['current_candlestick_doji'] == 1) |
                                    (df_dv['current_candlestick_dragon_fly_doji'] == 1) |
                                    (df_dv['current_candlestick_gravestone_doji'] == 1), 1, 0)
        return df_dv
    
    def get_summary(self, df):
        df_sum = df.copy()
        sum_stats = pd.DataFrame(df_sum.describe())
        num_non_zero = pd.DataFrame((df_sum != 0).astype(int).sum()).T
        num_non_zero = num_non_zero.rename(index={0: 'Num_non_zeros'})
        final_sum = pd.concat([sum_stats, num_non_zero], axis=0)[1:]
        final_sum = final_sum.T.reset_index().rename(columns={'index':'Feature'})
        return final_sum
    
    def scale_features(self, df, cols):
        df_scale = df.copy()
        min_max_scaler = MinMaxScaler()
        df_scale[cols] = min_max_scaler.fit_transform(df_scale[cols])
        df_scale = df_scale[cols]
        df_scale.columns = [x.replace('current', 'current_scaled') for x in df_scale.columns]
        return df_scale
    
    def do_pca(self, df, cols, num_comp, names):
        def_pca = PCA(n_components=num_comp)
        pca_out = def_pca.fit_transform(df[cols])
        #sum(def_pca.explained_variance_ratio_)
        cols_for_df = [f"current_{names}{x}" for x in range(1, num_comp + 1)]
        df_pca = pd.DataFrame(data = pca_out, columns = cols_for_df)
        return df_pca
    
    def combine_long(self):
        # first scan directory for new data
        files = os.listdir(f"{self.directory}")
        df_dates = [datetime.datetime.strptime(x, '%Y-%m-%d') for x in self.df['date'].tolist()]
        new_files = [x for x in files if (datetime.datetime.strptime(x, '%m-%d-%Y') not in df_dates) &
                     (datetime.datetime.strptime(x, '%m-%d-%Y') > min(df_dates))]
        if not new_files:
            print("Data is up to date")
        else:
            print(f"Detetected {len(new_files)} new files. Updating now.")
            for i in tqdm(new_files):
                df1 = self.usa_stocks(i)
                df2 = self.technical_signals(i, df1)
                #vix_df = self.get_vix()
                #df2 = df2.merge(vix_df, on='Date', how='left')
                df_updt = pd.concat([self.df, df2], axis=0)
                df_updt['date'] = pd.to_datetime(df_updt['date'])
                df_updt = df_updt[['date', 'Ticker'] + df_updt.drop(['date', 'Ticker'], axis=1).columns.tolist()]
                self.df = df_updt.sort_values(['Ticker', 'date']).reset_index().drop(['index'], axis=1)
            # add in vix
            vix_df = self.get_vix()
            self.df = self.df.merge(vix_df, on='date', how='left')
            # clean-up columns names
            candlesticks = ['signal_doji', 'signal_hammer', 'signal_long_lower_shadow', 'signal_long_upper_shadow',
                            'signal_inverted_hammer', 'signal_spinning_top_white', 'signal_spinning_top_black',
                            'signal_dragon_fly_doji', 'signal_gravestone_doji', 'signal_marubozu_white', 'signal_marubozu_black']
            patterns = ['signal_channel_down', 'signal_channel_up', 'signal_double_bottom', 'signal_double_top',
                        'signal_head_and_shoulders', 'signal_head_and_shoulders_inverse', 'signal_horizontal',
                        'signal_multiple_top', 'signal_multple_bottom', 'signal_triangle_ascending', 'signal_triangle_descending',
                        'signal_tl_resistance', 'signal_tl_support', 'signal_wedge', 'signal_wedge_down', 'signal_wedge_up']
            self.df.columns = [x.replace('signal', 'candlestick') if x in candlesticks else x for x in self.df.columns]
            self.df.columns = [x.replace('signal', 'pattern') if x in patterns else x for x in self.df.columns]
            self.df.columns = self.df.columns.str.replace('signal', 'indicator')
            self.df.columns = self.df.columns.str.replace('dv', 'indicator')
            self.df.columns = ['current_' + x if x not in ['date', 'Ticker', 'Sector', 'Industry'] else x for x in self.df.columns]
            self.df.columns = self.df.columns.str.lower()
            # add in day of week
            self.df['current_day_of_week'] = self.df['date'].dt.dayofweek
            # scale features
            feats_to_scale = ['current_market_cap', 'current_institutional_ownership', 'current_institutional_transactions',
                              'current_float_short', 'current_short_ratio', 'current_performance_week',
                              'current_performance_month', 'current_average_true_range', 'current_volatility_week',
                              'current_volatility_month', 'current_20_day_simple_moving_average',
                              'current_50_day_simple_moving_average', 'current_200_day_simple_moving_average',
                              'current_50_day_high', 'current_50_day_low', 'current_52_week_high', 'current_52_week_low',
                              'current_relative_strength_index_14', 'current_change_from_open', 'current_gap',
                              'current_average_volume', 'current_relative_volume', 'current_price', 'current_change',
                              'current_after_hours_change', 'current_vix', 'current_day_of_week']
            df_scaled = self.scale_features(self.df, feats_to_scale)
            self.df = pd.concat([self.df, df_scaled], axis=1)
            # replace all missing with nan
            self.df = self.df.fillna(0)
            # do pca
            cont_cols = [x for x in self.df.columns if x.startswith('current_scaled')]
            pci_cols = [x for x in self.df.columns if (('pattern' in x) | ('candle' in x) |
                                                       ('indicator' in x)) & (x.startswith('current'))]
            pca_df_cont = self.do_pca(self.df, cont_cols, 5, 'pca_cont')
            pca_df_pci = self.do_pca(self.df, pci_cols, 25, 'pca_pci')
            self.df = pd.concat([self.df, pca_df_cont, pca_df_pci], axis=1)
            # add in lag terms
            self.df = self.create_lag_feats(self.df, num_lags=1)
            # add dv variables
            self.df = self.create_dv(self.df)
            # write out data
            self.df.to_csv('df_long.csv', index=False)
        return self.df
    

In [3]:
df_init = pd.DataFrame()
init_date = '10-01-2021'

# initialize class
cld = CreateLongData(directory='D:/Finviz Data', df=df_init)
df_init = cld.usa_stocks(date=init_date)
df_init = cld.technical_signals(date=init_date, df_all=df_init)
df_init.to_csv('df_long.csv', index=False)
df_init

Ticker                  Sector  \
0          A              Healthcare   
1         AA         Basic Materials   
2        AAC               Financial   
3       AADI              Healthcare   
4       AAIC             Real Estate   
5        AAL             Industrials   
6       AAMC               Financial   
7       AAME               Financial   
8        AAN             Industrials   
9       AAOI              Technology   
10      AAON             Industrials   
11      AAPL              Technology   
12       AAT             Real Estate   
13      AATC              Technology   
14        AB               Financial   
15      ABBV              Healthcare   
16       ABC              Healthcare   
17      ABCB               Financial   
18      ABEO              Healthcare   
19      ABGI               Financial   
20      ABIO              Healthcare   
21       ABM             Industrials   
22      ABMD              Healthcare   
23      ABNB  Communication Services   
24       ABR             Real Estate   
25       ABT              Healthcare   
26      ABTX               Financial   
27      ABUS              Healthcare   
28        AC               Financial   
29      ACAD              Healthcare   
30      ACBI               Financial   
31       ACC             Real Estate   
32      ACCD              Healthcare   
33      ACCO             Industrials   
34      ACEL       Consumer Cyclical   
35      ACER              Healthcare   
36      ACET              Healthcare   
37      ACEV               Financial   
38       ACI      Consumer Defensive   
39      ACII               Financial   
40      ACIW              Technology   
41      ACLS              Technology   
42       ACM             Industrials   
43      ACMR              Technology   
44      ACNB               Financial   
45      ACOR              Healthcare   
46      ACQR               Financial   
47       ACR             Real Estate   
48      ACRE             Real Estate   
49      ACRS              Healthcare   
50      ACRX              Healthcare   
51      ACTG             Industrials   
52       ACU      Consumer Defensive   
53      ACVA              Technology   
54       ACY             Industrials   
55      ADBE              Technology   
56      ADER               Financial   
57      ADES             Industrials   
58       ADI              Technology   
59      ADIL              Healthcare   
60       ADM      Consumer Defensive   
61      ADMA              Healthcare   
62      ADMP              Healthcare   
63      ADMS              Healthcare   
64       ADN               Utilities   
65      ADOC               Financial   
66       ADP             Industrials   
67      ADPT              Healthcare   
68       ADS               Financial   
69      ADSK              Technology   
70       ADT             Industrials   
71      ADTN              Technology   
72      ADTX              Healthcare   
73       ADV  Communication Services   
74      ADVM              Healthcare   
75      ADXS              Healthcare   
76        AE                  Energy   
77       AEE               Utilities   
78      AEHR              Technology   
79      AEIS             Industrials   
80       AEL               Financial   
81       AEP               Utilities   
82       AES               Utilities   
83      AESE  Communication Services   
84      AEVA       Consumer Cyclical   
85       AEY              Technology   
86      AEYE              Technology   
87      AEZS              Healthcare   
88      AFBI               Financial   
89       AFG               Financial   
90       AFI             Industrials   
91      AFIB              Healthcare   
92      AFIN             Real Estate   
93       AFL               Financial   
94      AFRM              Technology   
95       AGC               Financial   
96      AGCB               Financial   
97      AGCO             Industrials   
98       AGE              Healthcare   
99    

In [4]:
cld = CreateLongData(directory='D:/Finviz Data', df=pd.read_csv('df_long.csv'))
df_long = cld.combine_long()
df_long

  0%|                                                                                                                                                                                                              | 0/13 [00:00<?, ?it/s]

Detetected 13 new files. Updating now.


100%|█████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 13/13 [00:15<00:00,  1.17s/it]


[*********************100%***********************]  1 of 1 completed


100%|███████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 1/1 [00:05<00:00,  5.35s/it]


date ticker      sector                industry  \
0     2021-10-01      A  Healthcare  Diagnostics & Research   
1     2021-10-04      A  Healthcare  Diagnostics & Research   
2     2021-10-05      A  Healthcare  Diagnostics & Research   
3     2021-10-06      A  Healthcare  Diagnostics & Research   
4     2021-10-07      A  Healthcare  Diagnostics & Research   
...          ...    ...         ...                     ...   
48330 2021-10-14   ZYXI  Healthcare         Medical Devices   
48331 2021-10-15   ZYXI  Healthcare         Medical Devices   
48332 2021-10-18   ZYXI  Healthcare         Medical Devices   
48333 2021-10-19   ZYXI  Healthcare         Medical Devices   
48334 2021-10-20   ZYXI  Healthcare         Medical Devices   

       current_market_cap  current_institutional_ownership  \
0                47687.70                            0.903   
1                46577.98                            0.903   
2                46782.80                            0.903   
3                46972.34                            0.903   
4                47482.88                            0.903   
...                   ...                              ...   
48330              430.93                            0.316   
48331              428.61                            0.317   
48332              428.25                            0.317   
48333              444.94                            0.317   
48334              446.01                            0.317   

       current_institutional_transactions  current_float_short  \
0                                  0.0100               0.0114   
1                                  0.0100               0.0114   
2                                  0.0100               0.0114   
3                                  0.0100               0.0114   
4                                  0.0100               0.0114   
...                                   ...                  ...   
48330                             -0.0003               0.1865   
48331                             -0.0015               0.1865   
48332                             -0.0015               0.1865   
48333                             -0.0015               0.1865   
48334                             -0.0015               0.1865   

       current_short_ratio  current_performance_week  ...  \
0                     2.07                   -0.0952  ...   
1                     2.07                   -0.0843  ...   
2                     2.06                   -0.0430  ...   
3                     2.06                   -0.0397  ...   
4                     2.07                   -0.0140  ...   
...                    ...                       ...  ...   
48330                11.70                    0.0989  ...   
48331                11.53                    0.0815  ...   
48332                11.61                    0.0797  ...   
48333                11.95                    0.1108  ...   
48334                12.40                    0.0874  ...   

       previous1_pca_pci22  previous1_pca_pci23  previous1_pca_pci24  \
0                      NaN                  NaN                  NaN   
1                -0.050033             0.033918             0.176511   
2                -0.001473            -0.007002            -0.031182   
3                -0.048655            -0.006349             0.031267   
4                -0.030008            -0.007827            -0.077060   
...                    ...                  ...                  ...   
48330             0.020831            -0.055438             0.100984   
48331            -0.202690            -0.025783            -0.059067   
48332            -0.011468            -0.027872            -0.044912   
48333            -0.028287            -0.004326             0.167848   
48334            -0.009330            -0.047281            -0.061687   

       previous1_pca_pci25  dv_5perc_inc_from_open  dv_2perc_inc_from_open  \
0                      NaN               

In [5]:
cld.get_summary(df_long)

Feature          mean  \
0                                   current_market_cap  1.329311e+04   
1                      current_institutional_ownership  6.542338e-01   
2                   current_institutional_transactions  6.631428e-02   
3                                  current_float_short  4.436760e-02   
4                                  current_short_ratio  4.693361e+00   
5                             current_performance_week  8.291692e-04   
6                            current_performance_month -9.038599e-03   
7                           current_average_true_range  2.578533e+00   
8                              current_volatility_week  3.703432e-02   
9                             current_volatility_month  3.824820e-02   
10                current_20_day_simple_moving_average -1.680287e-03   
11                current_50_day_simple_moving_average -5.174818e-03   
12               current_200_day_simple_moving_average -8.760136e-03   
13                                 current_50_day_high -1.308008e-01   
14                                  current_50_day_low  1.493353e-01   
15                                current_52_week_high -2.647195e-01   
16                                 current_52_week_low  8.647646e-01   
17                  current_relative_strength_index_14  5.004875e-01   
18                            current_change_from_open -8.950453e-04   
19                                         current_gap  2.232796e-03   
20                              current_average_volume  1.370308e+03   
21                             current_relative_volume  1.054704e+00   
22                                       current_price  1.218230e+02   
23                                      current_change  1.307053e-03   
24                          current_after_hours_change  6.312312e-04   
25                        current_pattern_channel_down  1.027438e-02   
26                          current_pattern_channel_up  1.039441e-02   
27                            current_candlestick_doji  2.717430e-02   
28                       current_pattern_double_bottom  1.068248e-02   
29                          current_pattern_double_top  1.032239e-02   
30                        current_indicator_downgrades  3.288763e-03   
31                   current_indicator_earnings_before  9.122116e-04   
32                          current_candlestick_hammer  3.478407e-02   
33                  current_pattern_head_and_shoulders  6.673548e-03   
34          current_pattern_head_and_shoulders_inverse  3.840891e-04   
35                  current_indicator_high_short_float  2.162902e-02   
36                          current_pattern_horizontal  1.147466e-02   
37                current_indicator_lt_3perc_above_low  2.236359e-01   
38               current_indicator_lt_3perc_below_high  2.613006e-01   
39                        current_indicator_major_news  8.714022e-03   
40                       current_indicator_most_active  2.878268e-02   
41                     current_indicator_most_volatile  2.542190e-02   
42                        current_pattern_multiple_top  6.097415e-03   
43                      current_pattern_multple_bottom  1.241088e-02   
44                          current_indicator_new_high  3.142329e-02   
45                           current_indicator_new_low  1.653984e-02   
46                        current_indicator_overbought  4.609069e-03   
47                          current_indicator_oversold  2.688624e-03   
48              current_indicator_price_above_20daysma  5.155436e-01   
49      current_indicator_price_crossed_above_20daysma  1.107857e-01   
50             current_indicator_recent_insider_buying  1.807619e-02   
51            current_indicator_recent_insider_selling  2.362148e-02   
52              current_indicator_relative_volume_gt_5  9.458194e-03   
53                       current_pattern_tl_resistance  7.969849e-03   
54                          current_pattern_tl_support  1.058646e-02   
55             

In [23]:
df_long[['date', 'ticker', 'previous1_pca_cont1']][df_long['ticker']=='ALKT']

date ticker  previous1_pca_cont1
1143 2021-10-11   ALKT                  NaN
1144 2021-10-12   ALKT             0.334827

In [3]:
# Additional feature ideas
    # exponential decay on features (major news etc.)
    # predicted current change from open or predicted current price as features
    # does PCA on one-hot features make sense?
    # more lagged features
    # keep features that are truly fixed over time like fundamentals as fixed effects and the remaining as group level slopes
    # include all fundamentals from finviz settings into pca
        # maybe use this as a random interecept intercept 

    
# Modeling pipeline
    # RNN
    # Mixed effect logistic regression
        # intercepts on industry, sector, ticker
    # Use output of above models as features for an xgboost with hyperparameter tuning for final prediction
    # autoregressive model
    
# performance tracking
    # what kind of stocks is the model predicting correctly the best? performance by sector
    # daily - precision, recall, f1 score, accuracy, auc 
    # sample size (denominatory for each performance metric)
    # daily - percent of stocks that closed higher

# output pca variance explained as more data is added/updated
    
# Dependent variable ideas
    # change from open (continuous)
    # change from previous close (continuous)
    # price (continuous)
    # test if class 0 is simply not class 1

# troubleshooting
    # some tickers are not being utilized as groups in me model
        # do they contain NAs and are being ignored?